In [1]:
from keras import *
import tensorflow as tf
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import matplotlib.pyplot as plt
from keras.layers import Activation, LeakyReLU
from tensorflow.keras.activations import sigmoid
from keras.utils.generic_utils import get_custom_objects
from keras import backend as K
from sklearn.preprocessing import StandardScaler
import os 
import statistics

In [2]:
os.chdir(os.getcwd())
train_folder = "Train/"

In [3]:
train = pd.read_csv(train_folder+"X_train.csv")
test = pd.read_csv(train_folder+"X_test.csv")
y_train = pd.read_csv(train_folder+"y_train.csv")
train['price'] = y_train[['price']]

In [4]:
import pandas_profiling
y_train.profile_report()

Render HTML: 100%|██████████| 1/1 [00:00<00:00,  2.17it/s]


In [5]:
train.describe()

Unnamed: 0      latitude     longitude  minimum_nights  \
count  33884.000000  33884.000000  33884.000000    33884.000000   
mean   16941.500000    393.742123   -767.324528        7.109904   
std     9781.612597   3773.366411   7123.758128       20.234836   
min        0.000000     40.499790 -74142.000000        1.000000   
25%     8470.750000     40.690427    -73.983503        1.000000   
50%    16941.500000     40.723645    -73.956025        3.000000   
75%    25412.250000     40.763910    -73.937005        5.000000   
max    33883.000000  40894.000000    -73.712990     1000.000000   

       number_of_reviews  reviews_per_month  calculated_host_listings_count  \
count       33884.000000       33884.000000                    33884.000000   
mean           23.391778           1.095455                        7.101080   
std            44.608022           1.610452                       32.746915   
min             0.000000           0.000000                        1.000000   
25%             1.000000           0.040000                        1.000000   
50%             5.000000           0.370000                        1.000000   
75%            24.000000           1.590000                        2.000000   
max           629.000000          58.500000                      327.000000   

       availability_365  Private_room  Entire_home/apt         price  
count      33884.000000  33884.000000     33884.000000  33884.000000  
mean         112.995839      0.456085         0.520127    153.605389  
std          131.641035      0.498075         0.499602    249.102710  
min            0.000000      0.000000         0.000000      0.000000  
25%            0.000000      0.000000         0.000000     69.000000  
50%           45.000000      0.000000         1.000000    106.000000  
75%          227.000000      1.000000         1.000000    175.000000  
max          365.000000      1.000000         1.000000  10000.000000

In [6]:
import pandas_profiling
train.profile_report()

Render HTML: 100%|██████████| 1/1 [00:03<00:00,  3.78s/it]


In [7]:
test.describe()

Unnamed: 0      latitude     longitude  minimum_nights  \
count  3765.00000   3765.000000   3765.000000     3765.000000   
mean   1882.00000    397.429772   -623.385344        7.717663   
std    1087.00621   3793.819578   6348.269973       31.688428   
min       0.00000     40.507080 -74124.000000        1.000000   
25%     941.00000     40.689430    -73.984260        1.000000   
50%    1882.00000     40.723370    -73.956270        2.000000   
75%    2823.00000     40.763420    -73.935150        5.000000   
max    3764.00000  40833.000000    -73.724350     1250.000000   

       number_of_reviews  reviews_per_month  calculated_host_listings_count  \
count        3765.000000        3765.000000                     3765.000000   
mean           22.546348           1.073421                        8.124568   
std            42.644924           1.553516                       37.043267   
min             0.000000           0.000000                        1.000000   
25%             1.000000           0.040000                        1.000000   
50%             5.000000           0.380000                        1.000000   
75%            24.000000           1.550000                        2.000000   
max           447.000000          20.940000                      327.000000   

       availability_365  Private_room  Entire_home/apt  
count       3765.000000   3765.000000      3765.000000  
mean         115.432669      0.451262         0.526959  
std          132.790393      0.497685         0.499339  
min            0.000000      0.000000         0.000000  
25%            0.000000      0.000000         0.000000  
50%           51.000000      0.000000         1.000000  
75%          231.000000      1.000000         1.000000  
max          365.000000      1.000000         1.000000

In [8]:
y_train.drop('Unnamed: 0',axis='columns',inplace=True)
train.drop('Unnamed: 0',axis='columns',inplace=True)
test.drop('Unnamed: 0',axis='columns',inplace=True)

In [9]:
from sklearn.utils import shuffle
train.drop(train[train['price'] == 10000].index, inplace = True) 
train.drop(train[train['price'] == 9999].index, inplace = True)

train = shuffle(train, random_state=42)
test = shuffle(test, random_state=42)
y_train = train[['price']]
train.drop(['price'], axis=1, inplace=True)
train.dtypes

latitude                          float64
longitude                         float64
minimum_nights                      int64
number_of_reviews                   int64
reviews_per_month                 float64
calculated_host_listings_count      int64
availability_365                    int64
Private_room                        int64
Entire_home/apt                     int64
dtype: object

In [10]:
y_train.shape

(33879, 1)

In [11]:
train.loc[train.latitude > 91, "latitude"] = train.latitude / 1000
train.loc[train.longitude < -181, "longitude"] = train.longitude / 1000
train.describe()

latitude     longitude  minimum_nights  number_of_reviews  \
count  33879.000000  33879.000000    33879.000000       33879.000000   
mean      40.728971    -73.952337        7.103161          23.394964   
std        0.054465      0.045810       20.223105          44.610534   
min       40.499790    -74.240840        1.000000           0.000000   
25%       40.690145    -73.983000        1.000000           1.000000   
50%       40.723090    -73.955700        3.000000           5.000000   
75%       40.763220    -73.936650        5.000000          24.000000   
max       40.913060    -73.712990     1000.000000         629.000000   

       reviews_per_month  calculated_host_listings_count  availability_365  \
count       33879.000000                    33879.000000      33879.000000   
mean            1.095611                        7.101981        112.996842   
std             1.610519                       32.749248        131.640565   
min             0.000000                        1.000000          0.000000   
25%             0.040000                        1.000000          0.000000   
50%             0.370000                        1.000000         45.000000   
75%             1.590000                        2.000000        227.000000   
max            58.500000                      327.000000        365.000000   

       Private_room  Entire_home/apt  
count  33879.000000     33879.000000  
mean       0.456094         0.520116  
std        0.498076         0.499603  
min        0.000000         0.000000  
25%        0.000000         0.000000  
50%        0.000000         1.000000  
75%        1.000000         1.000000  
max        1.000000         1.000000

In [ ]:
print('Minimum value of the target variable:', int(y_train.min()))
print('Maximum value of the target variable:', int(y_train.max()))
print('Target dims', y_train.shape)

In [ ]:
def preprocess_data(X, scaler=None):
    columns = X.columns
    """Preprocess input data by standardise features 
    by removing the mean and scaling to unit variance"""
    if not scaler:
        scaler = StandardScaler()
        scaler.fit(X)
    X[columns] = scaler.transform(X[columns])
    return X, scaler

In [ ]:
print('Train dims', train.shape)
print('Test dims', test.shape)
print('Target dims', y_train.shape)

In [ ]:
X_train, scaler = preprocess_data(train)
test_final, _ = preprocess_data(test, scaler)

In [ ]:
X_train, X_validation, y_train, y_validation = train_test_split(X_train, y_train, test_size=0.1, random_state=0)


In [ ]:
def NeuralNetwork(X, activation, n_outputs):
    inputs = Input(shape = (X.shape[1])) #T/X/Y/C)
    x = layers.Dense(64, activation = activation ) (inputs)
    x = layers.Dense(32, activation = activation) (x)
    x = layers.Dense(16, activation = activation) (x)
    x = layers.Dense(n_outputs, activation = 'relu') (x) 
    model = Model(inputs, x)
    model.compile(loss = 'mse', optimizer='adam', metrics = [tf.keras.metrics.RootMeanSquaredError()]) #
    return model

In [ ]:
def gelu(x):
    return 0.5 * x * (1 + tf.tanh(tf.sqrt(2 / np.pi) * (x + 0.044715 * tf.pow(x, 3))))
get_custom_objects().update({'gelu': Activation(gelu)})

# Add the alpha parameter of the Leaky-Relu function

get_custom_objects().update({'leaky-relu': Activation(LeakyReLU(alpha=0.2))})

# Add the Swish function

def swish(x, beta = 1):
    return (x * sigmoid(beta * x))
get_custom_objects().update({'swish': Activation(swish)})

act_func = ['relu', 'elu', 'leaky-relu', 'selu', 'gelu', 'swish']

In [ ]:
result = []

for activation in act_func:
    print('\nTraining with -->{0}<-- activation function\n'.format(activation))
    dims = y_train.shape[1]
    model = NeuralNetwork(activation=activation, X = X_train, n_outputs=dims)
        
    history = model.fit(X_train, y_train,
            batch_size=128,
            epochs=30,
            verbose=2,
            validation_data=(X_validation, y_validation))
        
    result.append(history)
    K.clear_session()
    del model

In [ ]:
rmse_finale = []
def risultati(activation_function, rmse):
    for i in range(len(activation_function)):
        print('RMSE of the activation function {} is {}'.format(activation_function[i], round(rmse[i], 5)))
        
def plot_act_func_results(results, activation_functions = []):
    plt.figure(figsize=(10,7))
    plt.style.use('dark_background')
    
    # Plot of the validation root mean squared error
    plt.figure(figsize=(10,10))
    
    for act_func in results:
        plt.plot(act_func.history['val_root_mean_squared_error'])
        rmse_finale.append(act_func.history['val_root_mean_squared_error'][-1])
    
    plt.title('Model MSE')
    plt.ylabel('Test MSE')
    plt.xlabel('Epoch')
    plt.legend(activation_functions)
    plt.show()

plot_act_func_results(result, act_func)


In [ ]:
risultati(act_func,rmse_finale)

In [ ]:
model = NeuralNetwork(activation='selu', X = X_train, n_outputs=dims)
model.summary()
history2 = model.fit(X_train, y_train,
          batch_size=128,
          epochs=30,
          verbose=1,
          validation_data=(X_validation, y_validation))

In [ ]:
y_predict = model.predict(test_final)


In [ ]:
y_predict

In [ ]:
import matplotlib.pyplot as plt

plt.figure()
plt.plot(history2.history['root_mean_squared_error'])
plt.plot(history2.history['val_root_mean_squared_error'])
plt.title('model rmse')
plt.ylabel('rmse')
plt.xlabel('epoch')
plt.legend(['train','val'], loc = 'upper left')
plt.show()

In [ ]:
np.savetxt(f'Gianmaria_Balducci_807141_score1.txt', y_predict, fmt='%1.3f')